In [37]:
using Flux
using Random, LinearAlgebra

# Set seed for reproducibility
Random.seed!(42)

# Dimensions
m, n, r = 10, 8, 8  # A is m x n, X is m x k, Y is k x n

# Generate a random matrix A
A = randn(m, n)

# Initialize learnable factors
X = randn(m, r)
Y = randn(r, n)

function custom_loss(A, X, Y)
    return norm(A-X*Y)^2
    #return norm(A-X*Y)^2 + norm(X)^2 + norm(Y)^2    
end 

model_loss = (X,Y) -> custom_loss(A,X,Y)

# Training loop
niterations = 5000
for epoch in 1:niterations

    gX, gY = gradient(model_loss, X, Y)
    
    @. X = X - 0.01*gX
    @. Y = Y - 0.01*gY
    
    # Print loss every 50 epochs
    if epoch % 50 == 0
        println("Epoch $epoch: Loss = ", model_loss(X, Y))
    end
end

opterr = model_loss(X,Y)

# Display learned X and Y
Usvd,Ssvd,Vsvd = svd(A)
svderr = norm(A-Usvd[:,1:r]*Diagonal(Ssvd[1:r])*Vsvd[:,1:r]')^2

@show opterr
@show svderr

Epoch 50: Loss = 2.091547823016724
Epoch 100: Loss = 0.5661487081197589
Epoch 150: Loss = 0.37969498421413045
Epoch 200: Loss = 0.29424961525867044
Epoch 250: Loss = 0.23736222031632534
Epoch 300: Loss = 0.1964354866301492
Epoch 350: Loss = 0.16601387453115432
Epoch 400: Loss = 0.14287411770926364
Epoch 450: Loss = 0.1249276797918005
Epoch 500: Loss = 0.11076102657341395
Epoch 550: Loss = 0.09938956930058786
Epoch 600: Loss = 0.09011258577555409
Epoch 650: Loss = 0.08242286358561295
Epoch 700: Loss = 0.07594817484624594
Epoch 750: Loss = 0.07041219966566804
Epoch 800: Loss = 0.06560780146151443
Epoch 850: Loss = 0.06137839646849488
Epoch 900: Loss = 0.05760476277001347
Epoch 950: Loss = 0.05419557903563848
Epoch 1000: Loss = 0.05108056173010772
Epoch 1050: Loss = 0.048205435866809476
Epoch 1100: Loss = 0.04552821297055821
Epoch 1150: Loss = 0.04301640904246799
Epoch 1200: Loss = 0.040644943537536414
Epoch 1250: Loss = 0.038394535145568016
Epoch 1300: Loss = 0.036250462521420154
Epoch 1

1.2555705456793983e-28

In [46]:
# This will evaluate the gradient of norm(A-XY^2) at a point X, Y
# Let's check against my "analytical" gradient...
X = ones(m,r)
Y = ones(r,n)
gX, gY = gradient(model_loss, X, Y)
gX
gX + (2*(A - X*Y)*Y')

10×8 Matrix{Float64}:
 0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0
 0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0
 0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0
 0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0
 0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0
 0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0
 0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0
 0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0
 0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0
 0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0

In [29]:
norm(X), norm(Y)

(3.8030981067374814, 3.803098106737481)

In [30]:
norm(A-X*Y)

2.6586124701944938

In [53]:

# Dimensions
m, n, r = 10, 8, 8  # A is m x n, X is m x k, Y is k x n

# Generate a random matrix A
A = randn(m, n)

# Initialize learnable factors
X = randn(m, r)
Y = randn(r, n)

function full_function(A, X, Y)
    #return norm(A-X*Y)^2
    return norm(A-X*Y)^2 + norm(X)^2 + norm(Y)^2    
end 

optimization_function = (X,Y) -> full_function(A,X,Y)

opt = Optimisers.Adam(0.01)
state = Optimisers.setup(opt, (X,Y))

# Training loop (Flux calls this epochs, but I don't like confusing them...)
niteration = 5000
for iteration in 1:niteration
    #@show X, Y

    grads = gradient(optimization_function, X, Y)
    
    state, (X,Y) = Optimisers.update(state, (X,Y), grads)
    
    # Print loss every 50 epochs
    if iteration % 50 == 0
        println("Iteration $iteration: Loss = ", optimization_function(X, Y))
    end
end

@show opterr = optimization_function(X,Y)
@show norm(A-X*Y)^2


Iteration 50: Loss = 179.60227608291302
Iteration 100: Loss = 95.79193142197144
Iteration 150: Loss = 71.33033035163707
Iteration 200: Loss = 57.27653930501515
Iteration 250: Loss = 47.99503153083923
Iteration 300: Loss = 41.955722482084234
Iteration 350: Loss = 38.00203752449347
Iteration 400: Loss = 35.352331740381516
Iteration 450: Loss = 33.566439779119
Iteration 500: Loss = 32.37618085148305
Iteration 550: Loss = 31.59633605079715
Iteration 600: Loss = 31.093976245108976
Iteration 650: Loss = 30.775308464352666
Iteration 700: Loss = 30.576066285058488
Iteration 750: Loss = 30.453310272875175
Iteration 800: Loss = 30.378869803582386
Iteration 850: Loss = 30.334512046759293
Iteration 900: Loss = 30.308581208014253
Iteration 950: Loss = 30.293729764249335
Iteration 1000: Loss = 30.285404187704813
Iteration 1050: Loss = 30.280838545929953
Iteration 1100: Loss = 30.278390015150972
Iteration 1150: Loss = 30.277105947348623
Iteration 1200: Loss = 30.276447430899296
Iteration 1250: Loss =

7.141659826689626

In [23]:
using Optim

In [ ]:
m = 10
n = 8
A = randn(m,n)
#A = Matrix(1.0I,m,n)
r = 2
myf = x -> matrix_approx_function(x, A, r)
myg! = (x, storage) -> matrix_approx_gradient!(x, storage, A, r)

soln = optimize(myf, myg!, ones(m*r+n*r), BFGS(), Optim.Options(f_tol = 1e-8))
#soln = optimize(myf, myg!, randn(m*r+n*r), BFGS(), Optim.Options(f_tol = 1e-8))
x = Optim.minimizer(soln)
@show soln
Uopt = reshape(x[(1:m*r)],m,r)
Vopt = reshape(x[(m*r+1):end],n,r)
objval = 2*myf(x)
opterr = norm(A-Uopt*Vopt')^2

Usvd,Ssvd,Vsvd = svd(A)
svderr = norm(A-Usvd[:,1:r]*Diagonal(Ssvd[1:r])*Vsvd[:,1:r]')^2
@show objval
@show opterr
@show svderr
; # hide final output in JuliaBox